In [ ]:
import numpy as np
import dill
from tqdm import tqdm
import gmsh
import sympy
from utils import is_extreme_boundary
import matplotlib.pyplot as plt
from scipy.sparse import lil_matrix
from scipy.sparse.linalg import spsolve
import plotly

### Load precomputed integrals

In [ ]:
poisson_functional = dill.load(
    open("../calculations/hermite_cubic_poisson_matrix", "rb")
)
integral_values = dill.load(
    open("../calculations/hermite_cubic_poisson_right_values", "rb")
)
basis = dill.load(open("../calculations/hermite_cubic_basis_transformed", "rb"))

### Run triangulation

In [339]:
gmsh.initialize()
gmsh.model.add("tri_mesh")

# Define points
point_mesh_size = .09
point_1 = gmsh.model.geo.addPoint(0, 0, 0, point_mesh_size)
point_2 = gmsh.model.geo.addPoint(1, 0, 0, point_mesh_size)
point_3 = gmsh.model.geo.addPoint(0, 1, 0, point_mesh_size)
point_4 = gmsh.model.geo.addPoint(-1, 0, 0, point_mesh_size)
point_5 = gmsh.model.geo.addPoint(0, -1, 0, point_mesh_size)


# Define circles
arc_1 = gmsh.model.geo.addCircleArc(point_2, point_1, point_3)
arc_2 = gmsh.model.geo.addCircleArc(point_3, point_1, point_4)
arc_3 = gmsh.model.geo.addCircleArc(point_4, point_1, point_5)
arc_4 = gmsh.model.geo.addCircleArc(point_5, point_1, point_2)


# Define line loop
circle = gmsh.model.geo.addCurveLoop([arc_1, arc_2, arc_3, arc_4])

# Define plane surface
plane = gmsh.model.geo.addPlaneSurface([circle])

gmsh.model.geo.synchronize()


# Make regular triangulation -->>
# gmsh.model.mesh.setTransfiniteCurve(arc_1, 4)
# gmsh.model.mesh.setTransfiniteCurve(arc_2, 4)
# gmsh.model.mesh.setTransfiniteCurve(arc_3, 4)
# gmsh.model.mesh.setTransfiniteCurve(arc_4, 4)
# gmsh.model.mesh.setTransfiniteSurface(plane)

physical_group_curves_tag = gmsh.model.addPhysicalGroup(1, [arc_1, arc_2, arc_3, arc_4], name="Boundary curves")
physical_group_surface_tag = gmsh.model.addPhysicalGroup(2, [plane], name="Surface")


# point_tag = point_1  # replace with your point's tag
# attractor_field = gmsh.model.mesh.field.add("Attractor")
# gmsh.model.mesh.field.setNumbers(attractor_field, "NodesList", [point_tag])
# threshold_field = gmsh.model.mesh.field.add("Threshold")
# gmsh.model.mesh.field.setNumber(threshold_field, "IField", attractor_field)
# gmsh.model.mesh.field.setNumber(threshold_field, "LcMin", 0.00000001)
# gmsh.model.mesh.field.setNumber(threshold_field, "LcMax", 0.1)
# gmsh.model.mesh.field.setNumber(threshold_field, "DistMin", 0.00000001)
# gmsh.model.mesh.field.setNumber(threshold_field, "DistMax", 0.3)
# gmsh.model.mesh.field.setAsBackgroundMesh(threshold_field)



# Create a Distance field
# distField = gmsh.model.mesh.field.add("Distance")
# gmsh.model.mesh.field.setNumbers(distField, "EdgesList", [arc_1, arc_2, arc_3, arc_4])

# thresField = gmsh.model.mesh.field.add("Threshold")
# gmsh.model.mesh.field.setNumber(thresField, "IField", distField)
# gmsh.model.mesh.field.setNumber(thresField, "LcMin", point_mesh_size)
# gmsh.model.mesh.field.setNumber(thresField, "LcMax", point_mesh_size/4)
# gmsh.model.mesh.field.setNumber(thresField, "DistMin", 0.0)
# gmsh.model.mesh.field.setNumber(thresField, "DistMax", 0.2)

# Set the Threshold field as the background field
# gmsh.model.mesh.field.setAsBackgroundMesh(thresField)


gmsh.model.mesh.generate(2)
gmsh.option.setNumber(name="Mesh.Smoothing", value=30)

gmsh.fltk.run()

In [340]:
boundary_node_tags, boundary_node_coords = gmsh.model.mesh.getNodesForPhysicalGroup(1, physical_group_curves_tag)
surface_node_tags, points = gmsh.model.mesh.getNodesForPhysicalGroup(2, physical_group_surface_tag)
points = points.reshape(-1, 3)[:, :-1]
boundary_node_tags = boundary_node_tags - 1

element_types, element_tags, element_node_tags = gmsh.model.mesh.getElements()
triangles = [nodes for elem_type, nodes in zip(element_types, element_node_tags) if elem_type == 2][0]
triangles = triangles.reshape(-1, 3).astype(int)
triangles = triangles - 1

# triangles = orient_batch(triangles)

vertex_marker_is_boundary = np.zeros(surface_node_tags.shape[0])
vertex_marker_is_boundary[boundary_node_tags] = 1

boundary_edges = [nodes for elem_type, nodes in zip(element_types, element_node_tags) if elem_type == 1][0]
boundary_edges = boundary_edges.reshape(-1, 2).astype(int)
boundary_edges = boundary_edges - 1

In [341]:
all_edges = triangles[:, [[0, 1], [1, 2], [0, 2]]].reshape(-1, 2)
all_edges = np.sort(all_edges, axis=-1)
all_edges, counts = np.unique(all_edges, axis=0, return_counts=True)
edge_marker_is_boundary = (counts == 1).astype(int)[:, None]

# Precond

In [342]:
tmp = points[triangles]
v1 = tmp[:, 1] - tmp[:, 0]
v2 = tmp[:, 2] - tmp[:, 0]
v3 = tmp[:, 2] - tmp[:, 1]

# get areas
areas = np.abs(v1[:, 0] * v2[:, 1] - v1[:, 1] * v2[:, 0]) / 2
P = (
    (v1**2).sum(axis=-1) ** 0.5 + (v2**2).sum(axis=-1) ** 0.5 + (v3**2).sum(axis=-1) ** 0.5
)

points_indices = np.arange(points.shape[0])

vertex_1 = np.where(points_indices[:, None] == triangles[:, 0])
vertex_2 = np.where(points_indices[:, None] == triangles[:, 1])
vertex_3 = np.where(points_indices[:, None] == triangles[:, 2])

map_vertex = np.concatenate([vertex_1[0], vertex_2[0], vertex_3[0]])
map_triangle = np.concatenate([vertex_1[1], vertex_2[1], vertex_3[1]])

cond = np.zeros(points.shape[0])

for p_index in points_indices:
    w = 2 * areas[map_triangle[map_vertex == p_index]]
    w = w / P[map_triangle[map_vertex == p_index]]
    w = w.mean()
    cond[p_index] = w
    
cond *= 0
cond += 1

In [343]:
x, y = sympy.symbols("x y", real=True)

In [344]:
right_part_values = np.zeros((points.shape[0], 3))

In [345]:
F = sympy.Float(1)
F_x = F.diff(x)
F_y = F.diff(y)

In [346]:
right_part_values[:, 0] = sympy.lambdify((x, y), F)(*points.T)
right_part_values[:, 1] = sympy.lambdify((x, y), F_x)(*points.T)
right_part_values[:, 2] = sympy.lambdify((x, y), F_y)(*points.T)

In [361]:
matrix = lil_matrix((3 * points.shape[0], 3 * points.shape[0]), dtype=np.float32)
b = np.zeros(3 * points.shape[0])

for idx, element in enumerate(tqdm(triangles)):
    x1, x2, x3 = points[element[0], 0], points[element[1], 0], points[element[2], 0]
    y1, y2, y3 = points[element[0], 1], points[element[1], 1], points[element[2], 1]

    right = right_part_values[element].flatten()

    FF = poisson_functional(x1, y1, x2, y2, x3, y3)
    ff = integral_values(x1, y1, x2, y2, x3, y3, *right)

    for trial_idx in range(3):

        if vertex_marker_is_boundary[element[trial_idx]] == True:
            matrix[3 * element[trial_idx] + 0, 3 * element[trial_idx] + 0] = 1
            b[3 * element[trial_idx] + 0] = 0

            # check whether the boundary point is 'extreme'
            is_extreme, direction = is_extreme_boundary(
                all_edges, points, edge_marker_is_boundary, element[trial_idx]
            )
            
            matrix[3 * element[trial_idx] + 1, 3 * element[trial_idx] + 1] = 1
            matrix[3 * element[trial_idx] + 2, 3 * element[trial_idx] + 2] = 1
            b[3 * element[trial_idx] + 1] = 0
            b[3 * element[trial_idx] + 2] = 0

        else:
            for trial_dof in range(3):
                for test_idx in range(3):
                    for test_dof in range(3):
                        matrix[
                            3 * element[trial_idx] + trial_dof,
                            3 * element[test_idx] + test_dof,
                        ] += (
                            FF[
                                3 * trial_idx + trial_dof, 3 * test_idx + test_dof
                            ] / cond[element[trial_idx]]**(0 if trial_dof == 0 else 1) / cond[element[test_idx]]**(0 if test_dof == 0 else 1)
                        )

            b[3 * element[trial_idx] + 0] -= ff[3 * trial_idx + 0, 0]
            b[3 * element[trial_idx] + 1] -= ff[3 * trial_idx + 1, 0]
            b[3 * element[trial_idx] + 2] -= ff[3 * trial_idx + 2, 0]

100%|██████████| 984/984 [00:00<00:00, 1421.53it/s]


In [348]:
c = spsolve(matrix.tocsc(), b)

In [349]:
np.linalg.cond(matrix.toarray())

8658.869

In [350]:
F =  c[0::3]
Fx = c[1::3] / cond**1
Fy = c[2::3] / cond**1

In [353]:
param = np.linspace(0, 1, 8)
tx, ty = np.meshgrid(param, param, indexing="ij")
mask = ty <= 1 - tx
tx = tx[mask]
ty = ty[mask]

In [354]:
X, Y, Z = [], [], []

for element in triangles:
    x1, x2, x3 = points[element[0], 0], points[element[1], 0], points[element[2], 0]
    y1, y2, y3 = points[element[0], 1], points[element[1], 1], points[element[2], 1]

    ptx = x1 + tx * (x2 - x1) + ty * (x3 - x1)
    pty = y1 + tx * (y2 - y1) + ty * (y3 - y1)

    ptz = basis(
        x1,
        y1,
        x2,
        y2,
        x3,
        y3,
        F[element[0]],
        Fx[element[0]],
        Fy[element[0]],
        F[element[1]],
        Fx[element[1]],
        Fy[element[1]],
        F[element[2]],
        Fx[element[2]],
        Fy[element[2]],
        tx,
        ty,
    )

    X.append(ptx)
    Y.append(pty)
    Z.append(ptz)

X = np.concatenate(X)
Y = np.concatenate(Y)
Z = np.concatenate(Z)

In [355]:
Z_true = -(1 - X**2 - Y**2)/4

In [356]:
np.abs(Z_true - Z).max()

0.007916234290474819

In [360]:
# Create a mesh plot with color by intensity

fig = plotly.graph_objs.Figure(data=[plotly.graph_objs.Mesh3d(x=X, y=Y, z=Z, intensity=Z)])

# Add layout options if needed
fig.update_layout(scene=dict(aspectmode="cube",),
                  width=600,
                  height=600)

# Show the plot
fig.show()

In [359]:
# fig = plotly.graph_objs.Figure(data=[
#         plotly.graph_objs.Mesh3d(x=gx, y=gy, z=gz)
#         for gx, gy, gz in zip(X.reshape(triangles.shape[0], -1), Y.reshape(triangles.shape[0], -1), Z.reshape(triangles.shape[0], -1))
#         ])

# # Add layout options if needed
# fig.update_layout(scene=dict(aspectmode="cube",),
#                   width=600,
#                   height=600)

# fig.show()